In [1]:
import geopandas as gpd
import plotly.graph_objects as go
import json
import plotly.express as px

df = gpd.read_file("../../data/mestske_casti/mestske_casti.geojson")

df.head()

objectid  kod_mc         nazev_mc   poskyt  id_poskyt    nazev_1  \
0         1  539449    Praha-Lipence  HMP-IPR         43    Lipence   
1         2  538361  Praha-Kolovraty  HMP-IPR         43  Kolovraty   
2         3  538531    Praha-Nedvězí  HMP-IPR         43    Nedvězí   
3         4  539864   Praha-Zbraslav  HMP-IPR         43   Zbraslav   
4         5  538078     Praha-Benice  HMP-IPR         43     Benice   

                                 globalid  shape_Length  shape_Area  \
0  {4241F642-D542-418C-8A51-D4FE4F2AA07F}      0.161585    0.001033   
1  {F644B455-44E5-43E2-A5EB-C278AE982752}      0.183836    0.000815   
2  {ACBE8874-6590-46DC-AD54-1D4C9D59A94C}      0.114296    0.000478   
3  {F3620CD3-1FB0-4810-B2A7-99ABA1C0E22E}      0.253182    0.001235   
4  {3CDCDC42-7B72-409D-9E5E-0943C10FAF72}      0.136700    0.000348   

                                            geometry  
0  MULTIPOLYGON (((14.36251 49.98035, 14.36255 49...  
1  MULTIPOLYGON (((14.63253 50.02687, 14.63271 50...  
2  MULTIPOLYGON (((14.64613 50.02813, 14.64629 50...  
3  MULTIPOLYGON (((14.39866 50.00841, 14.39877 50...  
4  MULTIPOLYGON (((14.59332 50.02589, 14.59384 50...

In [2]:
bounds = df.total_bounds
center_lat = (bounds[1] + bounds[3]) / 2
center_lon = (bounds[0] + bounds[2]) / 2

In [6]:
colors = px.colors.qualitative.Set3 + px.colors.qualitative.Pastel1 + px.colors.qualitative.Pastel2
num_polygons = len(df)
if num_polygons > len(colors):
    colors = (colors * ((num_polygons // len(colors)) + 1))[:num_polygons]

In [3]:
df_projected = df.to_crs(epsg=5514)
centroids_projected = df_projected.geometry.centroid

centroids_wgs84 = centroids_projected.to_crs(epsg=4326)
centroid_lons = [point.x for point in centroids_wgs84]
centroid_lats = [point.y for point in centroids_wgs84]

In [4]:
hover_texts = []
for idx, row in df.iterrows():
    name = row.get('nazev_1', f'District {idx}')
    hover_text = name
    hover_texts.append(hover_text)

In [7]:
import re
import html

fig = go.Figure()

fig.add_trace(go.Scattermap(
    lon=centroid_lons,
    lat=centroid_lats,
    mode="text",
    text=hover_texts,
    hoverinfo="text",
    marker=dict(size=50, opacity=0, color="red"),
    textfont=dict( size=12, color="black"),
    textposition="middle center",
    showlegend=False,
    name="Districts"
))

layers = []
for idx, (_, row) in enumerate(df.iterrows()):
    individual_geojson = {
        "type": "FeatureCollection",
        "features": [
            {
                "type": "Feature",
                "geometry": json.loads(gpd.GeoSeries([row.geometry]).to_json())["features"][0]["geometry"],
                "properties": row.drop('geometry').to_dict()
            }
        ]
    }

    color = colors[idx % len(colors)]
    rgb_values = re.findall(r'\d+', color)
    if len(rgb_values) >= 3:
        color_rgba = f"rgba({rgb_values[0]}, {rgb_values[1]}, {rgb_values[2]}, 0.6)"
    else:
        color_rgba = "rgba(135, 206, 235, 0.6)"

    layer = {
        "source": individual_geojson,
        "below": "traces",
        "type": "fill",
        "color": color_rgba,
        "line": {"width": 2},
    }
    layers.append(layer)

fig.update_layout(
    title="Městské části Praha",
    map=dict(
        center=dict(lat=center_lat, lon=center_lon),
        zoom=10,
        layers=layers,
    ),
    height=800,
    margin={"l": 0, "r": 0, "t": 50, "b": 0},
)

fig.show()


In [ ]:
import geopandas as gpd
import plotly.graph_objects as go
import json
import matplotlib.colors as mcolors
import numpy as np

df = gpd.read_file("../../data/mestske_casti/mestske_casti.geojson")

hover_texts = []
for idx, row in df.iterrows():
    name = row.get('nazev_1', f'District {idx}')
    hover_texts.append(name)

df['hover_text'] = hover_texts
df['district_id'] = range(len(df))

def rgb_string_to_tuple(rgb_str):
    match = re.match(r'rgb\((\d+),(\d+),(\d+)\)', rgb_str)
    r, g, b = map(int, match.groups())
    return r / 255, g / 255, b / 255

def generate_unique_colors(n):
    base_colors = px.colors.qualitative.Set3
    rgb_colors = [rgb_string_to_tuple(c) for c in base_colors]
    x = np.linspace(0, 1, len(rgb_colors))
    x_new = np.linspace(0, 1, n)
    r = np.interp(x_new, x, [c[0] for c in rgb_colors])
    g = np.interp(x_new, x, [c[1] for c in rgb_colors])
    b = np.interp(x_new, x, [c[2] for c in rgb_colors])
    return [mcolors.to_hex((r[i], g[i], b[i])) for i in range(n)]

num_districts = len(df)
colors_unique = generate_unique_colors(num_districts)

geojson_data = json.loads(df.to_json())

fig = go.Figure(go.Choroplethmap(
    geojson=geojson_data,
    locations=df['district_id'],
    z=df['district_id'],
    hovertext=df['hover_text'],
    hoverinfo="text",
    colorscale = [[i/(num_districts-1), colors_unique[i]] for i in range(num_districts)],
    marker=go.choroplethmap.Marker(
        line=dict(
            width=1,
            color='black'
        ),
        opacity=0.6
    ),
    showscale=False
))

bounds = df.total_bounds
center_lat = (bounds[1] + bounds[3]) / 2
center_lon = (bounds[0] + bounds[2]) / 2

fig.update_layout(
    title="Městské části Praha",
   map=dict(
        center=dict(lat=center_lat, lon=center_lon),
        zoom=10,
        layers=layers,
    ),
    height=800,
    margin={"l": 0, "r": 0, "t": 50, "b": 0},
)

fig.show()


In [ ]:
import geopandas as gpd
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.colors as mcolors
import json
import numpy as np
import re

df = gpd.read_file("../../data/mestske_casti/mestske_casti.geojson")

df = df.to_crs(epsg=5514)
centroids = df.geometry.centroid

df = df.to_crs(epsg=4326)
centroids = centroids.to_crs(epsg=4326)

df["district_id"] = range(len(df))
df["label"] = df["nazev_1"].fillna("Unknown")

geojson_data = json.loads(df.to_json())

base_colors = px.colors.qualitative.Pastel
colors_unique = (base_colors * (len(df) // len(base_colors) + 1))[:len(df)]
colorscale = [[i/(len(df)-1), colors_unique[i]] for i in range(len(df))]

fig = go.Figure()

fig.add_trace(go.Choroplethmap(
    geojson=geojson_data,
    locations=df["district_id"],
    z=df["district_id"],
    colorscale=colorscale,
    showscale=False,
    marker=dict(line=dict(width=1.5, color="white"), opacity=0.8),
    hoverinfo="skip",
    hovertemplate=None
))

fig.add_trace(go.Scattermap(
    lon=centroids.x,
    lat=centroids.y,
    mode="text",
    text=df["label"],
    textfont=dict(size=14, color="black", family="Arial Black"),
    textposition="middle center",
    hoverinfo="skip",
    showlegend=False
))

bounds = df.total_bounds
center = dict(lat=(bounds[1]+bounds[3])/2, lon=(bounds[0]+bounds[2])/2)

fig.update_layout(
    map=dict(
        style="white-bg",
        center=center,
        zoom=10,
    ),
    margin=dict(l=0, r=0, t=10, b=0),
    height=800
)

fig.show()


In [ ]:
import geopandas as gpd
import plotly.graph_objects as go
import json

df = gpd.read_file("../../data/mestske_casti/mestske_casti.geojson")

df = df.to_crs(5514)
centroids = df.geometry.centroid
df = df.to_crs(4326)
geojson = json.loads(df.to_json())


centroids = centroids.to_crs(4326)
df["id"] = df.index
df["name"] = df["nazev_1"].fillna("Unknown")

bounds = df.total_bounds
center = dict(lat=(bounds[1] + bounds[3]) / 2, lon=(bounds[0] + bounds[2]) / 2)

fig = go.Figure()

fig.add_trace(go.Choroplethmap(
    geojson=geojson,
    locations=df["id"],
    z=[1]*len(df),
    showscale=False,
    hovertemplate="",
    marker=dict(line=dict(width=1, color="#DDDDDD")),
    colorscale=[[0, "#b27286"], [1, "#b27286"]],
    name="districts"
))

fig.add_trace(go.Scattermap(
    lon=centroids.x,
    lat=centroids.y,
    mode="text",
    text=df["name"],
    textfont=dict(size=12, color="black"),
    hoverinfo="skip",
    showlegend=False
))

fig.add_trace(go.Scattermap(
    lon=[], lat=[],  # updated interactively
    mode="lines",
    line=dict(width=3, color="black"),
    hoverinfo="skip",
    showlegend=False,
    name="border-highlight"
))

fig.update_layout(
    map=dict(
        style="white-bg",
        center=center,
        zoom=10,
    ),
    height=900,
    margin=dict(l=0, r=0, t=0, b=0),
    clickmode="event+select"
)

def update_highlight(trace, points, selector):
    if points.point_inds:
        i = points.point_inds[0]
        coords = df.iloc[i].geometry.exterior.coords
        xs, ys = zip(*coords)
        fig.data[2].lon = xs
        fig.data[2].lat = ys

fig.data[0].on_click(update_highlight)

fig.show()


In [30]:
import re

fig = go.Figure()
df_projected = df.to_crs(epsg=5514)

row = df.iloc[0]
row_projected = df_projected.iloc[0]

centroid_projected = row_projected.geometry.centroid
centroid_wgs84 = gpd.GeoSeries([centroid_projected], crs="EPSG:5514").to_crs(epsg=4326).iloc[0]
centroid_lon = centroid_wgs84.x
centroid_lat = centroid_wgs84.y

fig.add_trace(go.Scattermap(
    lon=[centroid_lon],
    lat=[centroid_lat],
    mode="text",
    text=hover_texts,
    hoverinfo="skip",
    marker=dict(size=50, opacity=0, color="red"),
    textfont=dict( size=12, color="black"),
    textposition="middle center",
    showlegend=False,
    name="Districts"
))

individual_geojson = {
    "type": "FeatureCollection",
    "features": [
        {
            "type": "Feature",
            "geometry": json.loads(gpd.GeoSeries([row.geometry]).to_json())["features"][0]["geometry"],
            "properties": row.drop('geometry').to_dict()
        }
    ]
}

layer = {
    "source": individual_geojson,
    "below": "traces",
    "type": "fill",
    "color": "rgba(135, 206, 235, 0.6)",
    "line": {"width": 2},
}

fig.update_layout(
    title=row["nazev_1"],
    map=dict(
        center=dict(lat=centroid_lat, lon=centroid_lon),
        zoom=12,
        layers=[layer],
    ),
    height=800,
    margin={"l": 0, "r": 0, "t": 50, "b": 0},
)

fig.show()